# Apply manually set thresholds to retrieve possible candidate mutations

## Load data and packages

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import os
import re
from random import sample as random_sample

%matplotlib inline

In [2]:
#load data with fixed mutations removed
df = pd.read_csv('/Users/chrisgraves/Documents/Yeast_data/Sequencing/saved_dfs/combined_filtered.csv')
num_alleles = df.shape[0]/6
print('There are %d alleles' %num_alleles)
df.head()


There are 53765 alleles


Chromosome  Position               Alt  Time              Ref  Is_repeat  \
0          I      5068  ATTTTTTTTTTTTTTC     1  ATTTTTTTTTTTTTC          1   
1          I      5068  ATTTTTTTTTTTTTTC     3  ATTTTTTTTTTTTTC          1   
2          I      5068  ATTTTTTTTTTTTTTC     5  ATTTTTTTTTTTTTC          1   
3          I      5068  ATTTTTTTTTTTTTTC     7  ATTTTTTTTTTTTTC          1   
4          I      5068  ATTTTTTTTTTTTTTC     9  ATTTTTTTTTTTTTC          1   

   Read_depth  Num_ref  Num_alt  Freq_ref  Freq_alt  Qual_ref  Qual_alt  \
0         NaN      NaN        0       NaN         0       NaN       NaN   
1         NaN      NaN        0       NaN         0       NaN       NaN   
2         NaN      NaN        0       NaN         0       NaN       NaN   
3         NaN      NaN        0       NaN         0       NaN       NaN   
4         NaN      NaN        0       NaN         0       NaN       NaN   

  Treatment  Strain  
0         C       1  
1         C       1  
2         C       1  
3         C       1  
4         C       1

In [3]:
#Filter alleles

filtered = df.groupby(['Chromosome','Position','Alt','Treatment','Strain']).filter(lambda x: 
                ((list(x['Freq_alt'])[4] >=0.2) | (list(x['Freq_alt'])[5] >=0.2))
                & ((list(x['Read_depth'])[4] >= 20) | (list(x['Read_depth'])[5] >= 20))
                & ((list(x['Freq_alt'])[0] <= 0.1) & (list(x['Freq_alt'])[1] <= 0.1))                                                                   
                & ((list(x['Qual_alt'])[4]>=20) | (list(x['Qual_alt'])[5]>=20)) 
                & (list(x['Is_repeat'])[0] == 0))
    
after_filter = filtered.shape[0]/6
print('There are %d alleles, %d were removed by filter' %(after_filter,num_alleles-after_filter))
filtered.head(20)

There are 191 alleles, 53574 were removed by filter


Chromosome  Position    Alt  Time     Ref  Is_repeat  Read_depth  \
1644        III       135      A     1       C          0         NaN   
1645        III       135      A     3       C          0         NaN   
1646        III       135      A     5       C          0         NaN   
1647        III       135      A     7       C          0         NaN   
1648        III       135      A     9       C          0          25   
1649        III       135      A    12       C          0         NaN   
1662        III       253  ACACC     1  CCACAC          0         NaN   
1663        III       253  ACACC     3  CCACAC          0         NaN   
1664        III       253  ACACC     5  CCACAC          0         NaN   
1665        III       253  ACACC     7  CCACAC          0         NaN   
1666        III       253  ACACC     9  CCACAC          0          27   
1667        III       253  ACACC    12  CCACAC          0         NaN   
1668        III       272   ACCA     1     ACA          0         NaN   
1669        III       272   ACCA     3     ACA          0         NaN   
1670        III       272   ACCA     5     ACA          0          53   
1671        III       272   ACCA     7     ACA          0         NaN   
1672        III       272   ACCA     9     ACA          0          23   
1673        III       272   ACCA    12     ACA          0          23   
1680        III       277     CA     1      CC          0         NaN   
1681        III       277     CA     3      CC          0         NaN   

      Num_ref  Num_alt  Freq_ref  Freq_alt   Qual_ref   Qual_alt Treatment  \
1644      NaN        0       NaN  0.000000        NaN        NaN         C   
1645      NaN        0       NaN  0.000000        NaN        NaN         C   
1646      NaN        0       NaN  0.000000        NaN        NaN         C   
1647      NaN        0       NaN  0.000000        NaN        NaN         C   
1648       19        6  0.760000  0.240000  37.789474  35.833333         C   
1649      NaN        0       NaN  0.000000        NaN        NaN         C   
1662      NaN        0       NaN  0.000000        NaN        NaN         C   
1663      NaN        0       NaN  0.000000        NaN        NaN         C   
1664      NaN        0       NaN  0.000000        NaN        NaN         C   
1665      NaN        0       NaN  0.000000        NaN        NaN         C   
1666       21        6  0.777778  0.222222  37.857143  34.500000         C   
1667      NaN        0       NaN  0.000000        NaN        NaN         C   
1668      NaN        0       NaN  0.000000        NaN        NaN         C   
1669      NaN        0       NaN  0.000000        NaN        NaN         C   
1670       31       14  0.688889  0.311111  37.032258  31.214286         C   
1671      NaN        0       NaN  0.000000        NaN        NaN         C   
1672       13        6  0.684211  0.315789  38.230769  34.166667         C   
1673       11        9  0.550000  0.450000  38.454545  29.333333         C   
1680      NaN        0       NaN  0.000000        NaN        NaN         C   
1681      NaN        0       NaN  0.000000        NaN        NaN         C   

      Strain  
1644       1  
1645       1  
1646       1  
1647       1  
1648       1  
1649       1  
1662       1  
1663       1  
1664       1  
1665       1  
1666       1  
1667       1  
1668       1  
1669       1  
1670       1  
1671       1  
1672       1  
1673       1  
1680       1  
1681       1

In [7]:
#Remove alleles that were already manually screened in composite score analysis
screened = pd.read_csv('/Users/chrisgraves/Documents/Yeast_data/Sequencing/saved_dfs/screened_alleles_composite.csv')
allele_groups = filtered.groupby(['Chromosome','Position','Treatment','Strain'])

for row in screened.itertuples():
    chrom = row.CHROM
    pos = row.POS
    strain = row.Strain
    treatment = row.Treatment
    
    try:
        var_group = allele_groups.get_group((chrom,pos,treatment,strain))
    except KeyError:
        var_group = pd.DataFrame(columns = ['Chromosome','Position','Ref','Alt','Ref_count','Alt_count','Ref_freq','Alt_freq','N_calls'])
    
    if var_group.shape[0] != 0:
        filtered = filtered[~((filtered['Chromosome']==chrom)&(filtered['Position']==pos)&(filtered['Treatment']==treatment)&(filtered['Strain']==strain))]
        
        
after_filter2 = filtered.shape[0]/6
print('There are %d alleles, %d were removed by filter' %(after_filter2,after_filter-after_filter2))

There are 173 alleles, 18 were removed by filter


## Plot alleles that passed filters

In [7]:
%%javascript
IPython.OutputArea.auto_scroll_threshold = 9999;

<IPython.core.display.Javascript object>

In [8]:
allele_groups = filtered.groupby(['Chromosome','Position','Alt','Treatment','Strain'])

num_alleles = after_filter2
nrows = np.ceil(num_alleles/float(4))

counter = 1
fig = plt.figure(figsize=(56,nrows*10))
for name, allele in allele_groups:
    N = np.array(allele['Num_alt'])+np.array(allele['Num_ref'])

    x = list(allele['Time'])
    y = list(allele['Freq_alt'])
    err = 1.96*np.sqrt(np.divide((np.ones(6)-y)*y,N))
    qual = list(allele['Qual_alt'])

    ref = allele['Ref'].iloc[0]
    alt = allele['Alt'].iloc[0]
    treatment = allele['Treatment'].iloc[0]
    strain = str(allele['Strain'].iloc[0])
    chrom = allele['Chromosome'].iloc[0]
    pos = str(int(allele['Position'].iloc[0]))

    
    plt.subplot(nrows,4,counter)
    plt.ylabel('Frequency',fontsize=26,fontweight='bold')
    plt.xlabel('Time',fontsize=26,fontweight='bold')
    plt.ylim([-0.1,1.2])
    plt.yticks([0.0,0.2,0.4,0.6,0.8,1.0],size=24,fontweight='bold')
    plt.xlim([0,14])
    plt.xticks([0,2,4,6,8,10,12,14],size=24,fontweight='bold')
    plt.scatter(x,y,s=800,c=qual,cmap='YlOrRd')
    plt.clim(0,40)
    plt.style.use('bmh')
    plt.title('Strain: %s%s \n Chromosome %s \n Position %s \n %s \n to %s' %(treatment,strain,chrom,pos,ref,alt), fontsize=28,fontweight='bold')

    cb = plt.colorbar()
    cb.set_label(label='Quality score',fontsize=26,weight='bold')
    cb.set_ticks([0,5,10,15,20,25,30,35,40])
    cb.ax.tick_params(labelsize=24)
        
    (_, caps, _) = plt.errorbar(x,y,yerr=err,ls='None',color='k',capsize=5)
    for cap in caps:
        cap.set_markeredgewidth(2)

    for i in range(len(x)):
        if not np.isnan(N[i]):
            plt.text(x[i],1.1,int(N[i]),ha='center',fontsize = 23, fontweight='bold',bbox=dict(facecolor='none', edgecolor='black', boxstyle='round'))
        
    plt.tight_layout()
        
    counter = counter+1